<h3>Import Libraries</h3>

In [1]:
# This code is entirely taken from two Githubs. I just fixed the bug and used as my dataset.
from keras.backend.tensorflow_backend import set_session
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import TimeDistributed
from keras.layers import LSTM, Dropout
from keras import optimizers
import pandas as pd
import numpy as np
from datetime import datetime, date, timedelta
from sklearn.metrics import confusion_matrix, roc_curve, auc,accuracy_score
import matplotlib.pyplot as plt
from itertools import cycle
from keras.models import load_model
import itertools
import pickle

Using TensorFlow backend.


<h3>Basic Preprocessing</h3>

In [2]:
################################## Reading in the file, and Basic Processing

train_log= pd.read_csv('/Users/jyoti/OneDrive/server/log_train.csv')

z0 = list(map(lambda x : x.split('T')[0], train_log['time'].tolist())) ## Splitting the 'time' which is a time stamp into 'date' and 'time' 
train_log['date'] = z0

z1 = list(map(lambda x : x.split('T')[1], train_log['time'].tolist()))
train_log['time'] = z1



################################# PART 1 ###################################
################### Developing the Feature Set - Part 1 ####################
################################## getting a count of the type 'event' type - 'access', 'navigate', 'page close' etc.

unique_enrolment=np.unique(train_log['enrollment_id'])
unique_event=np.unique(train_log['event'])
unique_source=np.unique(train_log['source'])

date_range=np.unique(train_log['date'])

In [3]:
print(train_log)

         enrollment_id      time   source       event  \
0                    1  09:38:29   server    navigate   
1                    1  09:38:39   server      access   
2                    1  09:38:39   server      access   
3                    1  09:38:48   server      access   
4                    1  09:41:49  browser     problem   
5                    1  09:41:50  browser     problem   
6                    1  09:42:28  browser     problem   
7                    1  09:42:30  browser     problem   
8                    1  09:43:20  browser     problem   
9                    1  09:43:25  browser     problem   
10                   1  09:43:25   server     problem   
11                   1  09:43:40   server     problem   
12                   1  09:44:29  browser  page_close   
13                   1  06:21:04   server    navigate   
14                   1  06:21:16   server      access   
15                   1  06:21:16   server      access   
16                   1  06:21:3

In [4]:
fil = train_log[['enrollment_id', 'event', 'time']].groupby(['enrollment_id',  'event']).agg('count') 
fil = fil['time']
fil = fil.unstack()

In [5]:
print(fil)

event          access  discussion  navigate  page_close  problem  video  wiki
enrollment_id                                                                
1               107.0         NaN      25.0        66.0     87.0   29.0   NaN
3                79.0        26.0      14.0        22.0    138.0    9.0   NaN
4                64.0         NaN      15.0        10.0      6.0    4.0   NaN
5               226.0        34.0      30.0        87.0    170.0   86.0   NaN
6                12.0         NaN       5.0         2.0      2.0    2.0   NaN
7               203.0        33.0      20.0        60.0     94.0   69.0   NaN
9                71.0         NaN      12.0         6.0      6.0    2.0   NaN
12               46.0         1.0       6.0        43.0      NaN   31.0   NaN
13              200.0         4.0      15.0        25.0    150.0   69.0   NaN
14               60.0         NaN      20.0         5.0     12.0    5.0   NaN
16              168.0        28.0      40.0        20.0     64.0

In [6]:

unique_enrolment=np.unique(train_log['enrollment_id'])
unique_event=np.unique(train_log['event'])
unique_source=np.unique(train_log['source'])

date_range=np.unique(train_log['date'])


In [7]:
print(unique_enrolment)

[     1      3      4 ... 200901 200904 200905]


In [8]:
print(unique_event)

['access' 'discussion' 'navigate' 'page_close' 'problem' 'video' 'wiki']


In [9]:
print(unique_source)

['browser' 'server']


In [10]:
obj_data= pd.read_csv("/Users/jyoti/OneDrive/server/object.csv")
print(obj_data)

                              course_id                         module_id  \
0      SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  L1s4VseGlRT302GZlJNStvtJZnvnr3IJ   
1      SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  HxVne4dRqhXXf9FEsuUxVBG2THLkXgGV   
2      SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  3fpwAdewUyNZkLToSwy7eWQmmglHzA0G   
3      SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  qEdbIFRbbfpjN4tkWOq8kMsxES84yPfy   
4      SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  q9vSHnqnL8T6MSYy1QZ1d1v8gb7HqKIc   
5      SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  jChJZWA7TPrU7h1y5uZfnwajue9MzGBn   
6      SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  54D4zY2cdRyG83ZfykBka35LzNS04AXi   
7      SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  zDoPYVWL0APn1CAim3uMOBoSA6sGt9MZ   
8      SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  lFaL098pNcCMxay4b7YvzwmolqCVT03N   
9      SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  I6LKQXheMldlnI1vCTZBBVq3RxLAOxpE   
10     SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  0lrB7xh60Mnfp83JZY0GbnYiVgQIcdBz   
11     SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  W569V82FPFMc3YKyMh7mUoAaiYAESfci   

In [11]:
x = obj_data.to_numpy()
a = []
for i in x:
    p = (i[0], i[1], i[2])
    a.append(p)
ans = set(a)

j = list(ans) 
print(j)

[('1pvLqtotBsKv7QSOsLicJDQMHx3lui6d', 'dDBMK7tce9fzKMiICYjB61lJXhs83OV3', 'problem'), ('shM3Yy9vxHn2aqjSYfQXOcwGo0hWh3MI', '0rgm2MK7NJvOaDY4T9O1GOaBJGgWY6Ej', 'vertical'), ('q6A6QG7qMpyNcznyT2XaIxnfNGkZRxXl', 'J3fkURmpLOtJrzfwaFxYI6QrPcbVWief', 'video'), ('q6A6QG7qMpyNcznyT2XaIxnfNGkZRxXl', '30zaytMRnfjEGTCjQL8Ev2PIwJHkL6iP', 'discussion'), ('TAYxxh39I2LZnftBpL0LfF2NxzrCKpkx', 'zh7O43KlJqgwU229H76vGvonH2kh5fhl', 'video'), ('SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw', 'QxNUNRYAxPyGUYy2JR12DVcripoHsL2d', 'outlink'), ('a2E7NQC7nZB7WHEhKGhKnKvUWtsLAQzh', '60zOti8LqV0ysgPGaCPfZOdAYHfDLEsK', 'video'), ('9zpXzW9zCfU8KGBWkhlsGH8B8czISH4J', 'VqIb7DNyMeHjLktWST2RdbkW20iTh8hD', 'vertical'), ('shM3Yy9vxHn2aqjSYfQXOcwGo0hWh3MI', 'ubHxtkGp1GCzEuuCEm43RpvKO7afgPHV', 'discussion'), ('Wm3dddHSynJ76EJV6hyLYKGGRL0JF3YK', 'vQTKE2iAtv7KKKxvVSH0HYRhVEmzsZuh', 'sequential'), ('5X6FeZozNMgE2VRi3MJYjkkFK8SETtu2', 'ukhbdkwTr17nj1xBozAumJ1shYQqdPc9', 'problem'), ('HbeAZjZFFQUe90oTP0RRO0PEtRAqU3kK', 'E4bptx4EEJS9ojNqLf4U5

In [12]:
g = pd.DataFrame(j)
g.columns = ['course_id', 'object', 'category']
print(g)

                              course_id                            object  \
0      1pvLqtotBsKv7QSOsLicJDQMHx3lui6d  dDBMK7tce9fzKMiICYjB61lJXhs83OV3   
1      shM3Yy9vxHn2aqjSYfQXOcwGo0hWh3MI  0rgm2MK7NJvOaDY4T9O1GOaBJGgWY6Ej   
2      q6A6QG7qMpyNcznyT2XaIxnfNGkZRxXl  J3fkURmpLOtJrzfwaFxYI6QrPcbVWief   
3      q6A6QG7qMpyNcznyT2XaIxnfNGkZRxXl  30zaytMRnfjEGTCjQL8Ev2PIwJHkL6iP   
4      TAYxxh39I2LZnftBpL0LfF2NxzrCKpkx  zh7O43KlJqgwU229H76vGvonH2kh5fhl   
5      SpATywNh6bZuzm8s1ceuBUnMUAeoAHHw  QxNUNRYAxPyGUYy2JR12DVcripoHsL2d   
6      a2E7NQC7nZB7WHEhKGhKnKvUWtsLAQzh  60zOti8LqV0ysgPGaCPfZOdAYHfDLEsK   
7      9zpXzW9zCfU8KGBWkhlsGH8B8czISH4J  VqIb7DNyMeHjLktWST2RdbkW20iTh8hD   
8      shM3Yy9vxHn2aqjSYfQXOcwGo0hWh3MI  ubHxtkGp1GCzEuuCEm43RpvKO7afgPHV   
9      Wm3dddHSynJ76EJV6hyLYKGGRL0JF3YK  vQTKE2iAtv7KKKxvVSH0HYRhVEmzsZuh   
10     5X6FeZozNMgE2VRi3MJYjkkFK8SETtu2  ukhbdkwTr17nj1xBozAumJ1shYQqdPc9   
11     HbeAZjZFFQUe90oTP0RRO0PEtRAqU3kK  E4bptx4EEJS9ojNqLf4U5BVZvPoeDB84   

In [13]:
y = train_log.merge(g,on=['object'],how='left',indicator=True)
print(y)
y.columns

         enrollment_id      time   source       event  \
0                    1  09:38:29   server    navigate   
1                    1  09:38:39   server      access   
2                    1  09:38:39   server      access   
3                    1  09:38:48   server      access   
4                    1  09:41:49  browser     problem   
5                    1  09:41:50  browser     problem   
6                    1  09:42:28  browser     problem   
7                    1  09:42:30  browser     problem   
8                    1  09:43:20  browser     problem   
9                    1  09:43:25  browser     problem   
10                   1  09:43:25   server     problem   
11                   1  09:43:40   server     problem   
12                   1  09:44:29  browser  page_close   
13                   1  06:21:04   server    navigate   
14                   1  06:21:16   server      access   
15                   1  06:21:16   server      access   
16                   1  06:21:3

Index(['enrollment_id', 'time', 'source', 'event', 'object', 'date',
       'course_id', 'category', '_merge'],
      dtype='object')

In [14]:
y.columns


Index(['enrollment_id', 'time', 'source', 'event', 'object', 'date',
       'course_id', 'category', '_merge'],
      dtype='object')

In [15]:
y = y.replace(np.nan, 'unknown')
print(y)

         enrollment_id      time   source       event  \
0                    1  09:38:29   server    navigate   
1                    1  09:38:39   server      access   
2                    1  09:38:39   server      access   
3                    1  09:38:48   server      access   
4                    1  09:41:49  browser     problem   
5                    1  09:41:50  browser     problem   
6                    1  09:42:28  browser     problem   
7                    1  09:42:30  browser     problem   
8                    1  09:43:20  browser     problem   
9                    1  09:43:25  browser     problem   
10                   1  09:43:25   server     problem   
11                   1  09:43:40   server     problem   
12                   1  09:44:29  browser  page_close   
13                   1  06:21:04   server    navigate   
14                   1  06:21:16   server      access   
15                   1  06:21:16   server      access   
16                   1  06:21:3

In [16]:
fil = y[['enrollment_id', 'category','course_id','source','event', 'date', 'time']].groupby(['enrollment_id', 'category', 'course_id','source','event','date']).agg('count')
print(fil.head(30))

                                                                                      time
enrollment_id category   course_id                        source  event   date            
1             chapter    DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila server  access  2014-06-19     2
                                                                          2014-06-21     1
                                                                          2014-06-22     1
                                                                          2014-06-24     1
                                                                          2014-06-27     2
                                                                          2014-06-30     1
                                                                          2014-07-01     1
                                                                          2014-07-04     1
                                                                          2014-07-05     1

In [17]:
fil = fil['time']
print(fil)

enrollment_id  category    course_id                         source   event       date      
1              chapter     DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila  server   access      2014-06-19     2
                                                                                  2014-06-21     1
                                                                                  2014-06-22     1
                                                                                  2014-06-24     1
                                                                                  2014-06-27     2
                                                                                  2014-06-30     1
                                                                                  2014-07-01     1
                                                                                  2014-07-04     1
                                                                                  2014-07-05     1
                

In [18]:
################################## Adding chapter, sequential and unknown to the feature set

## Obtaning a unique tuple of <module_id, course_id>, enabling a clean left outer join in this step.
## Repeating <module_id, course_id> in the object.csv file, causes a wrong join on the module_id, which is needed to find the type of module accessed - 'chapter', 'sequential'
x = obj_data.to_numpy()
a = []
for i in x:
    p = (i[0], i[1], i[2])
    a.append(p)
ans = set(a)

j = list(ans) 

g = pd.DataFrame(j)
g.columns = ['course_id', 'object', 'category']
#g.to_csv('data/objectunique.csv', index = False) 
#l = g[[1, 2]]

y = train_log.merge(g,on=['object'],how='left',indicator=True)
y = y.replace(np.nan, 'unknown')

fil = y[['enrollment_id', 'category','course_id','source','event', 'date', 'time']].groupby(['enrollment_id', 'category', 'course_id','source','event','date']).agg('count') 
fil = fil['time']
fil[np.isnan(fil)]=0
#fil = fil.unstack()
fil=fil.reset_index()

In [19]:
print(fil)

         enrollment_id    category                         course_id   source  \
0                    1     chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server   
1                    1     chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server   
2                    1     chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server   
3                    1     chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server   
4                    1     chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server   
5                    1     chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server   
6                    1     chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server   
7                    1     chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server   
8                    1     chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server   
9                    1     chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server   
10                   1     chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server   
11                   1     p

In [20]:
fil.columns

Index(['enrollment_id', 'category', 'course_id', 'source', 'event', 'date',
       'time'],
      dtype='object')

In [24]:
tt = y
print(tt)
tt.drop(tt.columns[[2,3,4]],axis=1,inplace=True)
train_mat = tt.to_numpy()

         enrollment_id      time   source       event  \
0                    1  09:38:29   server    navigate   
1                    1  09:38:39   server      access   
2                    1  09:38:39   server      access   
3                    1  09:38:48   server      access   
4                    1  09:41:49  browser     problem   
5                    1  09:41:50  browser     problem   
6                    1  09:42:28  browser     problem   
7                    1  09:42:30  browser     problem   
8                    1  09:43:20  browser     problem   
9                    1  09:43:25  browser     problem   
10                   1  09:43:25   server     problem   
11                   1  09:43:40   server     problem   
12                   1  09:44:29  browser  page_close   
13                   1  06:21:04   server    navigate   
14                   1  06:21:16   server      access   
15                   1  06:21:16   server      access   
16                   1  06:21:3

In [25]:
def session_span(train_mat):
    dict_main = {}
    list_temp = []
    i=1
    prev=1
    for each in train_mat:
        i = each[0]
        if i == prev:
            x = (each[1])
            list_temp.append(x)
        else:
            dict_main[prev] = list_temp
            list_temp = []
            prev = i
            list_temp.append((each[1]))
    dict_main[prev] = list_temp
    
    ## Checking for each user, for each click, if the click is within a fifty minute window, 
    ## and qualifies as within the current session. Or is aprt of the next session.
    time_mat = []
    for key in dict_main.keys():
        tot_time = 0
        session = 1
        start = dict_main[key][0]
        end = start
        for i in range(1,len(dict_main[key])):
            t2 = datetime.strptime(dict_main[key][i], "%H:%M:%S")
            t1 = datetime.strptime(end, "%H:%M:%S")
            t0 = datetime.strptime(start, "%H:%M:%S")
            diff = (t2-t1).seconds
            if diff < 3000:
                end = dict_main[key][i]
            else:
                session+=1
                tot_time+=(t1-t0).seconds
                start = dict_main[key][i]
                end = start
        tot_time+=(t1-t0).seconds
        tot_time = tot_time/60
        abc = (key,session,tot_time)
        #print("In",abc)
        time_mat.append(abc)
    
    time_df = pd.DataFrame(time_mat)
    time_df.columns = ["enrollment_id","session","tot_time"]
    return time_df



In [26]:
time_df=session_span(train_mat)
fil = fil.merge(time_df,on=['enrollment_id'],how='left',indicator=True)
fil.drop(fil.columns[[9]],axis=1,inplace=True)

In [27]:
fil.to_csv('myfeatures.csv')

In [28]:
## From the truth_train.csv files - addinf the result coulmn
data = pd.read_csv('/Users/jyoti/OneDrive/server/myfeatures.csv')
result = pd.read_csv('/Users/jyoti/OneDrive/server/truth_train.csv', header = None)

In [29]:
data .head(20)

Unnamed: 0  enrollment_id category                         course_id  \
0            0              1  chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
1            1              1  chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
2            2              1  chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
3            3              1  chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
4            4              1  chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
5            5              1  chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
6            6              1  chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
7            7              1  chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
8            8              1  chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
9            9              1  chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
10          10              1  chapter  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
11          11              1  problem  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
12          12              1  problem  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
13          13              1  problem  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
14          14              1  problem  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
15          15              1  problem  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
16          16              1  problem  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
17          17              1  problem  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
18          18              1  problem  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   
19          19              1  problem  DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   

     source    event        date  time  session    tot_time  
0    server   access  2014-06-19     2       15  425.933333  
1    server   access  2014-06-21     1       15  425.933333  
2    server   access  2014-06-22     1       15  425.933333  
3    server   access  2014-06-24     1       15  425.933333  
4    server   access  2014-06-27     2       15  425.933333  
5    server   access  2014-06-30     1       15  425.933333  
6    server   access  2014-07-01     1       15  425.933333  
7    server   access  2014-07-04     1       15  425.933333  
8    server   access  2014-07-05     1       15  425.933333  
9    server   access  2014-07-10     1       15  425.933333  
10   server   access  2014-07-11     1       15  425.933333  
11  browser  problem  2014-06-14     6       15  425.933333  
12  browser  problem  2014-06-19     1       15  425.933333  
13  browser  problem  2014-06-22     4       15  425.933333  
14  browser  problem  2014-06-27    26       15  425.933333  
15  browser  problem  2014-07-04    20       15  425.933333  
16  browser  problem  2014-07-11    18       15  425.933333  
17   server  problem  2014-06-14     2       15  425.933333  
18   server  problem  2014-06-19     1       15  425.933333  
19   server  problem  2014-06-27     1       15  425.933333

In [30]:
result.head(5)

0  1
0  1  0
1  3  0
2  4  0
3  5  0
4  6  0

In [31]:

result.columns = ['enrollment_id', 'result']
ann_data= data.merge(result,on=['enrollment_id'],how='left')

In [32]:
ann_data

Unnamed: 0  enrollment_id    category  \
0                 0              1     chapter   
1                 1              1     chapter   
2                 2              1     chapter   
3                 3              1     chapter   
4                 4              1     chapter   
5                 5              1     chapter   
6                 6              1     chapter   
7                 7              1     chapter   
8                 8              1     chapter   
9                 9              1     chapter   
10               10              1     chapter   
11               11              1     problem   
12               12              1     problem   
13               13              1     problem   
14               14              1     problem   
15               15              1     problem   
16               16              1     problem   
17               17              1     problem   
18               18              1     problem   
19               19              1     problem   
20               20              1     problem   
21               21              1     problem   
22               22              1  sequential   
23               23              1  sequential   
24               24              1  sequential   
25               25              1  sequential   
26               26              1  sequential   
27               27              1  sequential   
28               28              1  sequential   
29               29              1  sequential   
...             ...            ...         ...   
1737689     1737689         200883     unknown   
1737690     1737690         200883     unknown   
1737691     1737691         200883     unknown   
1737692     1737692         200885     unknown   
1737693     1737693         200887  sequential   
1737694     1737694         200887     unknown   
1737695     1737695         200887     unknown   
1737696     1737696         200887     unknown   
1737697     1737697         200887       video   
1737698     1737698         200888  sequential   
1737699     1737699         200888     unknown   
1737700     1737700         200888     unknown   
1737701     1737701         200888     unknown   
1737702     1737702         200888     unknown   
1737703     1737703         200888     unknown   
1737704     1737704         200888       video   
1737705     1737705         200889     unknown   
1737706     1737706         200893     unknown   
1737707     1737707         200895     unknown   
1737708     1737708         200896     unknown   
1737709     1737709         200897     unknown   
1737710     1737710         200898     unknown   
1737711     1737711         200900     unknown   
1737712     1737712         200901  sequential   
1737713     1737713         200901     unknown   
1737714     1737714         200901     unknown   
1737715     1737715         200901     unknown   
1737716     1737716         200901       video   
1737717     1737717         200904     unknown   
1737718     1737718         200905     unknown   

                                course_id   source       event        date  \
0        DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server      access  2014-06-19   
1        DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server      access  2014-06-21   
2        DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server      access  2014-06-22   
3        DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server      access  2014-06-24   
4        DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server      access  2014-06-27   
5        DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server      access  2014-06-30   
6        DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server      access  2014-07-01   
7        DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server      access  2014-07-04   
8        DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server      access  2014-07-05   
9        DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server      access  2014-07-10   
10       DPnLzkJJqOOPRJfBxIHbQEERiYHu5ila   server

In [33]:
unique_CourseIds=np.unique(ann_data['course_id'])
unique_events=np.unique(ann_data['event'])

#en_id=ann_data['enrollment_id'][1]
activity_data=pd.DataFrame(columns=['enrollment_id', 'date','access', 'discussion', 'navigate', 'page_close','problem', 'video', 'wiki','session', 'tot_time', 'result'])

print(activity_data)

Empty DataFrame
Columns: [enrollment_id, date, access, discussion, navigate, page_close, problem, video, wiki, session, tot_time, result]
Index: []


In [35]:

def course_activity(en_id, co_id, ann_data,q,activity_data):
#    activity_data['enrollment_id']=en_id
    rows_to_consider=ann_data.loc[(ann_data['enrollment_id'] == en_id) & (ann_data['course_id'] == co_id) & (co_id!='unknown')]
    if (len(rows_to_consider)>0):
        dates=pd.read_csv('/Users/jyoti/OneDrive/server/date.csv')
        course_dates=dates.loc[(dates['course_id']==co_id)]
        start_date=course_dates['from'][course_dates.index[0]]
        end_date=course_dates['to'][course_dates.index[0]]
        y1=start_date.split('-')[0]
        m1=start_date.split('-')[1]
        d1=start_date.split('-')[2]
        y2=end_date.split('-')[0]
        m2=end_date.split('-')[1]
        d2=end_date.split('-')[2]
        dd1 = datetime(int(y1), int(m1), int(d1))
        dd2 = datetime(int(y2), int(m2), int(d2))
        listdates = divide_date(dd1, dd2, 8)
        end_date=date = datetime.strptime(listdates[q].split(' ')[0], '%Y%m%d').strftime('%Y-%m-%d')
        course_dates=pd.date_range(start_date, end_date).tolist()
        aa=0
        dd=0
        nn=0
        ww=0
        bb=0
        vv=0
        pp=0
        for l in range(len(course_dates)):
    #        activity_data['enrollment_id']=f"{course_dates[l].date():%Y-%m-%d}" 
            date_rows=rows_to_consider.loc[(rows_to_consider['date'] == f"{course_dates[l].date():%Y-%m-%d}")]
    #        if(len(date_rows)==0):
    #            print
    #            activity_data.append({'enrollment_id':en_id, 'date': f"{course_dates[l].date():%Y-%m-%d}", 'access': 0, 'discussion':0, 'navigate':0,'page_close':0, 'problem':0, 'video':0, 'wiki':0, 'session':0,'tot_time':0},ignore_index=True)
    ##            for k in range(len(unique_events)):
    ##                activity_data[unique_events[k]]=0
    ##                activity_data['tot_time']=0
    #        else:
            aa1=date_rows.loc[(date_rows['event']=='access')]
            aa=aa+np.sum(aa1['time'])
            dd1=date_rows.loc[(date_rows['event']=='discussion')]
            dd=dd+np.sum(dd1['time'])     
            nn1=date_rows.loc[(date_rows['event']=='navigate')]
            nn=nn+np.sum(nn1['time'])
            pp1=date_rows.loc[(date_rows['event']=='page_close')]
            pp=pp+np.sum(pp1['time'])
            bb1=date_rows.loc[(date_rows['event']=='problem')]
            bb=bb+np.sum(bb1['time'])
            vv1=date_rows.loc[(date_rows['event']=='video')]
            vv=vv+np.sum(vv1['time'])            
            ww1=date_rows.loc[(date_rows['event']=='wiki')]
            ww=ww+np.sum(ww1['time'])            
    #            activity_data['tot_time']=date_rows['tot_time'][date_rows['tot_time'].index[0]]
    #            for k in range(len(unique_events)):
    #                aa=date_rows.loc[(date_rows['event']==unique_events[k])]
    #                print(np.sum(activity_rows['time']))
    #                activity_rows=date_rows.loc[(date_rows['event']==unique_events[k])]
    #                activity_data[unique_events[k]]=np.sum(activity_rows['time'])
#            if(len(date_rows)>0):
        activity_data=activity_data.append({'result':rows_to_consider['result'][rows_to_consider['result'].index[0]],'enrollment_id':en_id, 'date': f"{course_dates[1].date():%Y-%m-%d}", 'access': aa, 'discussion':dd, 'navigate':nn,'page_close':pp, 'problem':bb, 'video':vv, 'wiki':ww,'session':rows_to_consider['session'][rows_to_consider['session'].index[0]], 'tot_time':rows_to_consider['tot_time'][rows_to_consider['tot_time'].index[0]]}, ignore_index=True)
#    else:
#        activity_data=activity_data.append({'enrollment_id':en_id, 'date': f"{course_dates[l].date():%Y-%m-%d}", 'access': aa, 'discussion':dd, 'navigate':nn,'page_close':pp, 'problem':bb, 'video':vv, 'wiki':ww,'session':0, 'tot_time':0}, ignore_index=True)
#    
#     activity_data.drop( activity_data.columns[[0]],axis=1,inplace=True)  
    return activity_data
def remove_tack(dates_list):
  # given a list of dates in form YYYY-MM-DD return a list of strings in form 'YYYYMMDD'
  tackless = []
  for d in dates_list:
    s = str(d)
    tackless.append(s[0:4]+s[5:7]+s[8:])
  return tackless
def divide_date(date1, date2, intervals):
  dates = [date1]
  delta = (date2-date1).total_seconds()/4
  for i in range(0, intervals):
    dates.append(dates[i] + timedelta(0,delta))
  return remove_tack(dates)

In [ ]:
# do it separately for all the courses and save the results.
co_id=5
# #for co_id in range(100):
# #    print(co_id)
co_id1=ann_data['course_id'][co_id]
for en_id in range(len(unique_enrolment)):
  print(en_id)
  for q in range(1,9):
    print(q)
    en_id1=unique_enrolment[en_id]
    activity_data=course_activity(en_id1, co_id1, ann_data,q,activity_data)

0
1
2
3
4
5
6
7
8
1
1
2
3
4
5
6
7
8
2
1
2
3
4
5
6
7
8
3
1
2
3
4
5
6
7
8
4
1
2
3
4
5
6
7
8
5
1
2
3
4
5
6
7
8
6
1
2
3
4
5
6
7
8
7
1
2
3
4
5
6
7
8
8
1
2
3
4
5
6
7
8
9
1
2
3
4
5
6
7
8
10
1
2
3
4
5
6
7
8
11
1
2
3
4
5
6
7
8
12
1
2
3
4
5
6
7
8
13
1
2
3
4
5
6
7
8
14
1
2
3
4
5
6
7
8
15
1
2
3
4
5
6
7
8
16
1
2
3
4
5
6
7
8
17
1
2
3
4
5
6
7
8
18
1
2
3
4
5
6
7
8
19
1
2
3
4
5
6
7
8
20
1
2
3
4
5
6
7
8
21
1
2
3
4
5
6
7
8
22
1
2
3
4
5
6
7
8
23
1
2
3
4
5
6
7
8
24
1
2
3
4
5
6
7
8
25
1
2
3
4
5
6
7
8
26
1
2
3
4
5
6
7
8
27
1
2
3
4
5
6
7
8
28
1
2
3
4
5
6
7
8
29
1
2
3
4
5
6
7
8
30
1
2
3
4
5
6
7
8
31
1
2
3
4
5
6
7
8
32
1
2
3
4
5
6
7
8
33
1
2
3
4
5
6
7
8
34
1
2
3
4
5
6
7
8
35
1
2
3
4
5
6
7
8
36
1
2
3
4
5
6
7
8
37
1
2
3
4
5
6
7
8
38
1
2
3
4
5
6
7
8
39
1
2
3
4
5
6
7
8
40
1
2
3
4
5
6
7
8
41
1
2
3
4
5
6
7
8
42
1
2
3
4
5
6
7
8
43
1
2
3
4
5
6
7
8
44
1
2
3
4
5
6
7
8
45
1
2
3
4
5
6
7
8
46
1
2
3
4
5
6
7
8
47
1
2
3
4
5
6
7
8
48
1
2
3
4
5
6
7
8
49
1
2
3
4
5
6
7
8
50
1
2
3
4
5
6
7
8
51
1
2
3
4
5
6
7
8
52
1
2
3
4
5
6
7
8
53


In [ ]:


################################## writing result - 1 - dropout, 0 - completed


result.columns = ['enrollment_id', 'result']
ann_data= data.merge(result,on=['enrollment_id'],how='left')
#data['result'] = result['result']
ann_data.to_csv('myfeatures_ann.csv', index = False) ## Writing the 14 features with enrollment ID, and result to a file.

unique_CourseIds=np.unique(ann_data['course_id'])
unique_events=np.unique(ann_data['event'])

#en_id=ann_data['enrollment_id'][1]
activity_data=pd.DataFrame(columns=['enrollment_id', 'date','access', 'discussion', 'navigate', 'page_close','problem', 'video', 'wiki','session', 'tot_time', 'result'])


# do it separately for all the courses and save the results.
co_id=5

co_id1=ann_data['course_id'][co_id]
for en_id in range(len(unique_enrolment)):
  print(en_id)
  for q in range(1,9):
    print(q)
    en_id1=unique_enrolment[en_id]
    activity_data=course_activity(en_id1, co_id1, ann_data,q,activity_data)

################################## Normalisation
## All the data is brought into a range of 0 - 1
nodate_activity_data=pd.DataFrame(columns=['access', 'discussion', 'navigate', 'page_close','problem', 'video', 'wiki','session', 'tot_time', 'result'])
nodate_activity_data['access']=activity_data['access']
nodate_activity_data['discussion']=activity_data['discussion']
nodate_activity_data['navigate']=activity_data['navigate']
nodate_activity_data['page_close']=activity_data['page_close']
nodate_activity_data['problem']=activity_data['problem']
nodate_activity_data[ 'video']=activity_data[ 'video']
nodate_activity_data['wiki']=activity_data['wiki']
nodate_activity_data['session']=activity_data['session']
nodate_activity_data['tot_time']=activity_data['tot_time']
nodate_activity_data['result']=activity_data['result']

X=pd.DataFrame(columns=['access', 'discussion', 'navigate', 'page_close','problem', 'video', 'wiki','session', 'tot_time'])
#nodate_activity_data=pd.DataFrame(columns=['access', 'discussion', 'navigate', 'page_close','problem', 'video', 'wiki','session', 'tot_time', 'result'])
X['access']=nodate_activity_data['access']
X['discussion']=nodate_activity_data['discussion']
X['navigate']=nodate_activity_data['navigate']
X['page_close']=nodate_activity_data['page_close']
X['problem']=nodate_activity_data['problem']
X[ 'video']=nodate_activity_data[ 'video']
X['wiki']=nodate_activity_data['wiki']
X['session']=nodate_activity_data['session']
X['tot_time']=nodate_activity_data['tot_time']


y=nodate_activity_data['result']+1

Xtrain=X[:20000]
y_train=y[:20000]
X_test=X[20000:]
y_test=y[20000:]





X_tr=[]
y_tr=[]
l=0
while (l <len(Xtrain)-3):
    print(l)
    tmp=[]
    tmp.append(Xtrain.values[l])
    tmp.append(Xtrain.values[l+1])
    tmp.append(Xtrain.values[l+2])
    tmp.append(Xtrain.values[l+3])
    tmp.append(Xtrain.values[l+4])
    tmp.append(Xtrain.values[l+5])
    tmp.append(Xtrain.values[l+6])
    tmp.append(Xtrain.values[l+7])
    # tmp.append(Xtrain.values[l+8])
    X_tr.append(np.array(tmp))
    if(y_train[l]==1):
        y_tr.append([1,0])
    if(y_train[l]==2):
        y_tr.append([0,1])  
    l+=8
    
X_tr=np.array(X_tr)
y_tr=np.array(y_tr)



X_ts=[]
y_ts=[]
l=0
while (l <len(X_test)-3):
    print(l)
    tmp=[]
    tmp.append(X_test.values[l])
    tmp.append(X_test.values[l+1])
    tmp.append(X_test.values[l+2])
    tmp.append(X_test.values[l+3])
    tmp.append(X_test.values[l+4])
    tmp.append(X_test.values[l+5])
    tmp.append(X_test.values[l+6])
    tmp.append(X_test.values[l+7])
    # tmp.append(X_test.values[l+8])
    X_ts.append(np.array(tmp))
    if(y_test[20000+l]==1):
        y_ts.append([1,0])
    if(y_test[20000+l]==2):
        y_ts.append([0,1])  
    l+=8
    
X_ts=np.array(X_ts)
y_ts=np.array(y_ts)

activity_data.to_csv('myactivity8'+str(co_id)+'_ann.csv', index = False) ## Writing the 14 features with enrollment ID, and result to a file.
# This is the dataset on which I am working. I am working for course_ID = 5

<h3><b>References</b></h3>

1) https://github.com/Siddhant085/modelling-MOOC-dropout/blob/master/code.py 
95% code is taken from Reference[1] and two function are taken from another github. I don't remember exactly from which git I took the code. Sorry for that!!. But, the entire code of processing is the merge of two githubs. I just fixed the bug and used it as my dataset.